In [1]:
import json
import os
from pymongo import MongoClient
import codecs
import pandas as pd
import gensim
from gensim.models import phrases
from gensim.utils import lemmatize
import en_core_web_sm
from sklearn.feature_extraction.stop_words import ENGLISH_STOP_WORDS
from nltk.corpus import stopwords
from sklearn.externals import joblib

In [2]:
client = MongoClient()
db = client.lingbuzz
papers = db.get_collection('papers')

# Keyword extraction
Some words are more relevant for doc summarization than others. These words have the following properties:

* occur in abstract
* occur in keyword list (tokenized)
* occur in title (remove standard stopwords)
* occur in conclusion (remove standard stopwords)
* authors

Maybe also include following:

* first occurence at the beginning of the document (presumably these are the same as in the abstract...)
* high TFIDF score (to be determined per document and added to the list of top-k-words on a doc by doc base)
* words that revealed to be topic-relevant in topic modeling

For the classification: remove standard stopwords from my stopword list and take all sentences that contain these words for the non-relevant sentences target !! my stopword list was made with agressively tokenized words. Think about whether you want that.

In [3]:
def build_trigram_model(corpus):
    corpus = lemmer(nlp(corpus))
    bigram = phrases.Phrases(corpus, min_count=20, threshold=17)
    bigram_phraser = phrases.Phraser(bigram)
    trigram = phrases.Phrases(bigram_phraser[corpus], min_count=20, threshold=17)
    trigram_phraser = phrases.Phraser(trigram)
    return bigram_phraser, trigram_phraser

def punct_space(token):
    """
    helper function to eliminate punctuation, spaces and numbers.
    """
    return token.is_punct or token.is_space or token.like_num

#def remove_stopwords(tigrammized):
#    no_stop = [[term for term in sent if term not in my_stopwords] for sent in trigrammized]
 #   return no_stop
    
def remove_stopwords(stuff):
    # gives list of strings. Vectorizer needs this.
    out = []
    for sent in stuff:
        for term in sent:
            if term not in my_stopwords:
                out.append(term)
    return out

def remove_stopwords2(stuff):
    # gives list of list of strings. Phraser needs this.
    out = []
    for sent in stuff:
        out.append([term for term in sent if term not in my_stopwords])
    return out

def trigrammer(doc):
    tokens = nlp(doc)
    lemmas = lemmer(tokens)
    tokens_ = bigrams[lemmas]
    trigrammized = trigrams[tokens_]
    return [j for j in trigrammized]

def lemmer(tokens):
    """
    lemmatize words
    """
    word_space = []
    for sent in tokens.sents:
        sentence = []
        for token in sent:
            if not punct_space(token):
                if token.lemma_=='-PRON-':
                    sentence.append(token.lower_)
                else:
                    sentence.append(token.lemma_.strip('-'))
        word_space.append(sentence)
    return word_space

def my_tokenizer(doc):
    trigrammized = trigrammer(doc)
    return trigrammized

In [4]:
with open('lingbuzz.json') as f:
    meta_data = json.load(f)

In [5]:
meta_data[:4]

[{'abstract': ['In this response to Erlewine & Gould 2016, we show that an account of internally-headed relative clauses using Inverse Trace Conversion and the maximal informativeness semantics for definites of von Fintel et al. 2014 does not derive the observed interpretations when the internal head is quantified by certain downward entailing quantifiers and no interpretation at all for non-monotonic and some upward entailing quantifiers. We then argue that the cases that Erlewine & Gould(2016) claim to be a newly identified interpretation of internally-headed relatives are actually headless relatives.'],
  'authors': ['Keir Moulton', 'Junko Shimoyama'],
  'keywords': ['internally-headed relative clauses; quantification; maximal informativeness; trace conversion; entailment; headless relative clauses, semantics, syntax'],
  'published': ['McGill/SFU'],
  'title': 'On the Inverse Trace Conversion and maximal informativeness analysis of Japanese internally-headed relative clauses: A rep

In [6]:
for di in meta_data:
        papers.update_one({'title': di['title']}, {'$set': {"abstract": di['abstract']}})

In [7]:
keywords = []
titles = []
authors = []

for doc in papers.find():
    keywords+=(doc['keywords'])
    titles.append(doc['title'])
    authors+=(doc['authors'])

In [8]:
abstracts = []
for doc in papers.find({'abstract':{'$exists': True}}):
    abstracts+=doc['abstract']

In [9]:
conclusions = []
for doc in papers.find({'paper':{'$exists': True}}):
    paper = doc['paper']
    to_match = doc['title']
    index_conclusion = paper.lower().rfind('conclusion')
    index_bibliography = paper.lower().rfind('bibliography')
    if index_conclusion != -1 and index_bibliography != -1:
        conclusion = paper[index_conclusion: index_bibliography]
        papers.update_one({'title': to_match}, {'$set': {'conclusion': conclusion }})
        conclusions.append(conclusion)

In [10]:
standard_stopwords = set(list(ENGLISH_STOP_WORDS)+list(stopwords.words('english')))

In [11]:
stopwords = joblib.load('../Aca_paper/notebooks/stopwords')

In [12]:
standard_stopwords

{'a',
 'about',
 'above',
 'across',
 'after',
 'afterwards',
 'again',
 'against',
 'ain',
 'all',
 'almost',
 'alone',
 'along',
 'already',
 'also',
 'although',
 'always',
 'am',
 'among',
 'amongst',
 'amoungst',
 'amount',
 'an',
 'and',
 'another',
 'any',
 'anyhow',
 'anyone',
 'anything',
 'anyway',
 'anywhere',
 'are',
 'aren',
 'around',
 'as',
 'at',
 'back',
 'be',
 'became',
 'because',
 'become',
 'becomes',
 'becoming',
 'been',
 'before',
 'beforehand',
 'behind',
 'being',
 'below',
 'beside',
 'besides',
 'between',
 'beyond',
 'bill',
 'both',
 'bottom',
 'but',
 'by',
 'call',
 'can',
 'cannot',
 'cant',
 'co',
 'con',
 'could',
 'couldn',
 'couldnt',
 'cry',
 'd',
 'de',
 'describe',
 'detail',
 'did',
 'didn',
 'do',
 'does',
 'doesn',
 'doing',
 'don',
 'done',
 'down',
 'due',
 'during',
 'each',
 'eg',
 'eight',
 'either',
 'eleven',
 'else',
 'elsewhere',
 'empty',
 'enough',
 'etc',
 'even',
 'ever',
 'every',
 'everyone',
 'everything',
 'everywhere',
 'exc

In [70]:
from string import digits
import re, string

# note: to get rid of unicode and wrongly tokenized words in the docs themselves, I have to find a way to get rid 
# of all words that contain punctuation except '-', and then substitute '-' by ''.

def eliminate_non_english_words(s):
    """takes list of words and eliminates all words that contain non-english characters, digits or punctuation"""
    english_words = []
    for word in s:
        try:
            word.encode(encoding='utf-8').decode('ascii')
            # if re.sub('-', '', word).isalpha():
                # english_words.append(re.sub('[%s]' % re.escape(string.punctuation), '', word))
            word = re.sub('[%s]' % re.escape(string.punctuation), '', word)
            if word.isalpha():
                english_words.append(word) 
        except UnicodeDecodeError:
            pass
    return english_words

In [34]:
def remove_standard_stopwords(li):
    """takes list of texts and returns list of words without standard stopwords, punctuation or digits"""
    words = []
    for text in li:
        no_weirdness = eliminate_non_english_words(text.split())
        for w in no_weirdness:
            if w.lower() not in standard_stopwords:
                words.append(w.lower())
        #words+= eliminate_non_english_words([w.lower() for w in text.split() if w.lower() not in standard_stopwords])
    return words

In [44]:
keywords_flat = remove_standard_stopwords([re.sub('[%s]' % re.escape(string.punctuation), '', w) for k in keywords for w in k.split()])

In [32]:
abstracts_flat = remove_standard_stopwords(abstracts)

paper
argue
existence
null
resumption
kaqchikel
mayan
showing
new
empirical
facts
language
strategies
make
possessor
interrogative
type
possessor
wh
basegenerated
speccp
heads
resumptive
chain
type
undergoes
movement
speccp
present
set
paradoxical
cases
resumption
kaqchikel
displays
movement
properties
simple
clause
longdistance
dependency
suggest
domain
locality
relevant
resumptive
dependencies
kaqchikel
constrained
widely
discussed
resumptive
languages
like
irish
hebrew
specifically
proposed
resumptive
pronoun
kaqchikel
licensed
clause
clausemate
condition
resumptive
chains
ccrc
ccrc
explain
resumptive
dependencies
kaqchikel
display
island
effects
irish
hebrew
suggesting
ccrc
operative
irish
hebrew
natural
language
possible
minds
language
uncovers
cognitive
landscape
nature
attempts
demonstrate
language
reveal
hidden
logical
texture
diverse
types
mentality
nonhumans
contrary
popular
belief
widely
held
assumption
mainstream
cognitive
science
language
humanly
unique
introduces
anthropo

accept
violations
certain
island
constraints
unacceptable
languages
crosslinguistically
tested
acceptability
whextraction
island
types
complex
np
subject
adjunct
relative
clause
rc
islands
clear
evidence
subject
adjunct
island
effects
whextraction
failed
evidence
norwegians
accept
whextraction
complex
nps
rcs
participants
judged
whextraction
complex
nps
rcs
unacceptable
subject
adjunct
island
violations
pattern
effects
norwegian
paralleled
island
effects
recent
experimental
work
documented
languages
like
english
italian
sprouse
et
al
sprouse
et
al
norwegian
judgments
consistently
differed
prior
findings
island
type
whetherislands
results
reveal
norwegians
exhibit
significant
interindividual
variation
sensitivity
whetherisland
effects
participants
exhibiting
sensitivity
whetherisland
violations
whatsoever
discuss
implications
findings
universalist
approaches
island
constraints
suggest
ways
reconciling
results
previous
observations
offer
systematic
experimental
framework
future
research


pph
tested
case
studies
different
external
sandhi
processes
studies
contribute
general
understanding
relationship
variability
syntactic
prosodic
lexical
factors
study
investigates
effect
word
boundaries
prosodic
position
phonetic
pauses
variation
high
vowel
devoicing
hvd
tokyo
japanese
statistical
modeling
hvd
patterns
corpus
spontaneous
speech
suggests
factors
jointly
affect
hvd
position
prosodic
phrase
modulates
effect
speech
rate
lexical
frequency
hvd
proposed
distinct
processes
underlie
hvd
sensitive
segmental
content
upcoming
word
interconsonantal
hvd
triggered
strong
prosodic
boundaries
phrasefinal
hvd
view
variation
explained
pph
production
planning
effects
interconsonantal
hvd
second
case
study
factors
previously
associated
external
sandhi
variation
tested
directly
syntactic
structure
lexical
frequency
factors
shown
affect
speech
planning
according
pph
affect
external
sandhi
production
experiment
examine
effect
clause
boundary
realization
wordfinal
coronal
stops
north
american


assume
functional
category
invisible
grammar
mandarin
order
account
behaviors
nominal
arguments
argues
lack
dp
projections
mandarin
recent
comparative
semantics
suggests
sign
language
makes
use
logical
resources
spoken
language
richer
mechanisms
iconic
enrichment
thought
speech
analyzed
tandem
iconic
gestures
expressive
parity
regained
speech
sign
comparison
signwithiconicity
speechwithgestures
turns
complex
iconic
enrichments
nonatissue
status
attested
interaction
logical
operators
argue
status
iconic
enrichments
constrained
parameters
enrichment
effected
internal
modification
expression
internal
lengthening
word
loooong
english
sign
grow
asl
semantic
status
particular
atissue
enrichment
external
addition
expression
internal
case
cospeech
gestures
english
make
atissue
contribution
status
presupposition
supplement
enrichment
separate
time
slot
separatetimeslot
trivial
presupposed
atissue
supplemental
generalization
assessed
basis
vocal
iconicity
spoken
language
iconic
modulations
sign


ground
appears
construct
statelike
configuration
addition
configurations
emerge
pronominal
grounds
different
marking
e
genitive
given
restrictorless
internal
structure
pronouns
entails
movement
axparts
movement
place
internal
structure
ground
intimately
related
place
thought
sort
relational
noun
microcomparative
data
southern
italian
varieties
pronominal
grounds
possession
marking
pronominal
possessors
relational
nouns
kinship
terms
andor
body
parts
argue
properties
sign
language
grammar
counterparts
nonsigners
intuitions
gestures
including
ones
probably
uncommon
despite
intrinsic
limitations
gestures
compared
fullfledged
sign
languages
access
rules
gesture
research
focuses
cospeech
gestures
cooccur
spoken
words
focus
instead
prospeech
gestures
fully
replace
spoken
words
make
fullfledged
semantic
contribution
like
signs
argue
gestural
loci
emulate
properties
sign
language
loci
positions
signing
space
realize
discourse
referents
arbitrary
number
loci
distinction
speaker
addressee
person

...

readings
existentials
pins
novel
semantics
cardinal
determiners
counting
values
individual
concept
worlds
analysis
shown
predict
descriptive
generalizations
summative
existentials
including
highly
restricted
circumstances
arise
unorthodox
semantics
cardinals
relies
argued
independently
motivated
grammatical
theories
faithfully
incorporate
cumulative
effects
optimality
theory
different
means
suggested
account
cumulativity
constraint
interaction
viz
local
constraint
conjunction
harmonic
grammar
present
paper
considers
cumulative
effects
morphology
differential
argument
encoding
syntax
longdistance
extraction
shows
existing
analyses
terms
local
constraint
conjunction
transferred
harmonic
grammar
analyses
cumulative
constraint
interaction
selectively
switched
local
conjunction
analyses
impossible
principled
reasons
harmonic
grammar
analyses
consequently
harmonic
grammar
explicitly
designed
capture
cumulative
effects
turns
approach
systematically
unable
derive
certain
kind
cumulativity
prev

couched
simplified
form
discourse
representation
theory
shown
solution
consistent
general
theories
cognition
shed
novel
light
nature
flnflb
distinction
certain
psych
constructions
formed
regular
pattern
languages
psychological
predicate
phrase
physical
predicate
psych
constructions
words
like
ving
vant
adjectives
english
french
phrasal
like
desiderative
construction
finnish
study
adjectives
marrant
jawdropping
effing
vphy
ing
psycha
phyinsidepsych
constructs
literally
mean
causes
physical
effect
usually
triggered
emotionsensation
actually
mean
causes
psych
meaning
exceptional
contrary
ving
forms
mean
mean
causes
unexpected
meaning
forms
introduce
cause
participant
lead
investigate
syntax
object
experiencer
morphological
syntactic
constructions
discuss
semantics
prenominal
zero
zero
new
emails
inbox
zero
quantifier
like
giving
zero
regular
numeral
semantics
possible
desirable
formulate
analysis
consequences
existence
zero
numeral
profound
consequences
linguistic
semantics
conclude
fact


modal
prepositional
complementizer
dui
types
clauses
systematically
properties
nonfinite
clauses
languages
intrinsically
embedded
ban
prodrop
clause
boundaries
invisible
binding
disallow
speakeroriented
adverb
epistemic
modal
restrictions
distribution
particles
indicate
finite
markers
language
tense
case
marker
paper
argues
finite
clauses
speakeroriented
properties
nonfinite
ones
instead
nonfinite
clauses
exhibit
higherclauseoriented
properties
identifying
role
speaker
finiteness
distinction
reveals
capacity
finite
clauses
capacity
marked
overtly
paper
focuses
languages
exhibit
processes
copy
epenthesis
specifically
similarity
copy
vowel
host
extends
prosodic
suprasegmental
resemblance
argue
copy
vowels
hosts
strive
identity
prosodic
properties
drive
prosodic
identity
cause
misapplication
assignment
properties
stress
pitch
length
explain
effects
argue
successful
analysis
copy
epenthesis
involve
correspondence
relation
following
kitto
lacy
proposal
successfully
predicts
extant
typology


artefactual
complexity
precludes
strongest
possible
natural
constraints
characterizations
human
faculty
language
theorizing
based
linguistic
action
intent
leads
thinner
simplified
directly
empirical
argumentation
compared
indirections
necessitated
complex
syntactic
analysis
based
central
configurational
syntax
inclusion
linguistic
action
intent
generative
rules
enables
deepening
understanding
role
generative
constructs
ccommand
merge
computational
facility
underlies
human
language
revealing
new
level
significance
basic
claims
careful
examination
linguistic
intent
methodology
greatly
reduce
entropy
syntactic
semantic
pragmatic
theory
independently
explaining
plethora
ill
formed
sentences
straightforward
way
leaving
tractable
set
separate
theoretical
problems
disciplines
scientific
validity
enhanced
revising
architecture
generative
linguistics
bidirectional
soundmeaning
connection
functional
connection
linguistic
action
intention
external
linguistic
representation
introduction
summary
al

nyorobon
poppo
pijotto
current
study
reports
experiments
test
patterns
productive
minds
general
japanese
speakers
experiments
ii
tendency
hold
english
speakers
experiment
results
effect
mora
length
clearly
observed
japanese
speakers
english
speakers
effects
voiced
obstruents
observed
clearly
japanese
speakers
clearly
english
speakers
analyses
familiarity
pokemon
influence
responses
suggesting
possibility
speakers
learn
soundsymbolic
patterns
particular
set
lexical
items
pokemon
research
value
argue
general
project
useful
undergraduate
phonetics
education
related
corpus
study
kastner
started
developing
contemporary
description
hebrew
verb
framework
distributed
morphology
dm
goal
article
present
somewhat
different
approach
dm
understanding
hebrew
roots
order
work
entire
set
hebrew
verbs
section
classify
large
number
verb
classes
conjugations
conjugations
subsumes
number
smaller
classes
section
second
conjugations
section
follows
discussion
fourth
fifth
conjugations
section
explain
mediev

In [45]:
'is' in keywords_flat

False

In [35]:
titles_flat = remove_standard_stopwords(titles)

In [67]:
authors

['Yusuke Imanishi',
 'Prakash Mondal',
 'Lida Veselovska',
 'Halldor Armann Sigurdsson',
 'Halldor Armann Sigurdsson',
 'Lida Veselovska',
 'Aaron Doliana',
 'Sandhya Sundaresan',
 'Lida Veselovska',
 'Philippe Schlenker',
 'Itamar Kastner',
 'Vera Zu',
 'Kyle Gorman',
 'Charles Yang',
 'Guilherme Duarte Garcia',
 'Dominique Sportiche',
 'Norbert Francis',
 'Georg Höhn',
 'Dave Kush',
 'Terje Lohndal',
 'Jon Sprouse',
 'Asia Pietraszko',
 'William Merrill',
 'Jonathan Bobaljik',
 'Uli Sauerland',
 'Holden Härtl',
 'Heiko Seeliger',
 'Philippe Schlenker',
 'Maren Berg Grimstad',
 'Brita Ramsevik Riksem',
 'Terje Lohndal',
 'Tor Anders Aafarli',
 'Juliet Stanton',
 'Richard Breheny',
 'Nathan Klinedinst',
 'Jacopo Romoli',
 'Yasutada Sudo',
 'Philipp Weisser',
 'Mandy Simons',
 'Nicholas Longenbaugh',
 'James N. Collins',
 'Hadas Kotek',
 'Matthew Barros',
 'Joseph Emonds',
 "Roberta D'Alessandro",
 'Klaus Abels',
 'Klaus Abels',
 'Veneeta Dayal',
 'Ana Ojea',
 'Andrew Ira Nevins',
 'Chr

In [82]:
def flatten_authors(li):
    english_words = []
    for author in li:
        for word in author.split():
            english_words.append( re.sub('[%s]' % re.escape(string.punctuation), '', word))
    words = []
    for w in english_words:
        if len(w)>1:
            if w.lower() not in standard_stopwords:
                words.append(w.lower())
            #words+= eliminate_non_english_words([w.lower() for w in text.split() if w.lower() not in standard_stopwords])
    return words

In [83]:
# I will also flatten out the authors, to glue composite names together and seperate first names from last names. 
# In the text we will usually find the last name only.
authors_flat = flatten_authors(authors)

In [84]:
authors_flat

['yusuke',
 'imanishi',
 'prakash',
 'mondal',
 'lida',
 'veselovska',
 'halldor',
 'armann',
 'sigurdsson',
 'halldor',
 'armann',
 'sigurdsson',
 'lida',
 'veselovska',
 'aaron',
 'doliana',
 'sandhya',
 'sundaresan',
 'lida',
 'veselovska',
 'philippe',
 'schlenker',
 'itamar',
 'kastner',
 'vera',
 'zu',
 'kyle',
 'gorman',
 'charles',
 'yang',
 'guilherme',
 'duarte',
 'garcia',
 'dominique',
 'sportiche',
 'norbert',
 'francis',
 'georg',
 'höhn',
 'dave',
 'kush',
 'terje',
 'lohndal',
 'jon',
 'sprouse',
 'asia',
 'pietraszko',
 'william',
 'merrill',
 'jonathan',
 'bobaljik',
 'uli',
 'sauerland',
 'holden',
 'härtl',
 'heiko',
 'seeliger',
 'philippe',
 'schlenker',
 'maren',
 'berg',
 'grimstad',
 'brita',
 'ramsevik',
 'riksem',
 'terje',
 'lohndal',
 'tor',
 'anders',
 'aafarli',
 'juliet',
 'stanton',
 'richard',
 'breheny',
 'nathan',
 'klinedinst',
 'jacopo',
 'romoli',
 'yasutada',
 'sudo',
 'philipp',
 'weisser',
 'mandy',
 'simons',
 'nicholas',
 'longenbaugh',
 'jam

In [36]:
flat_conclusions = remove_standard_stopwords(conclusions)
## the conclusions contain too much trash, I won't extract keywords from them.

In [92]:
top_k_words = set(titles_flat + abstracts_flat + keywords_flat + authors_flat + ['v2'])

In [93]:
len(top_k_words)

24977

In [94]:
joblib.dump(top_k_words, 'top_k_words')

['top_k_words']

In [60]:
'phonology)?' in top_k_words

False

In [95]:
top_k_words

{'raisingtoobject',
 'jerzy',
 'valentim',
 'lattice',
 'elected',
 'continuing',
 'ripley',
 'relativised',
 'hornscales',
 'negation',
 'mereology',
 'paragraph',
 'institute',
 'polish',
 'wak',
 'cookies',
 'fred',
 'regarding',
 'ahmad',
 'spuy',
 'focuse',
 'equidistance',
 'borjars',
 'conspiracies',
 'galani',
 'pictorial',
 'orderpreserving',
 'dishonesty',
 'roehrs',
 'preps',
 'milan',
 'derivability',
 'gappeddegree',
 'standardization',
 'broad',
 'maxim',
 'web',
 'bytes',
 'mismatched',
 'introduction',
 'quadratic',
 'numeralphrase',
 'relativizers',
 'calculates',
 'chordfrequency',
 'contents',
 'phone',
 'verbtype',
 'idiolectaldialectal',
 'deaccentuation',
 'categoryneutral',
 'ls',
 'octaviamaria',
 'lim',
 'ambulance',
 'usable',
 'vacuity',
 'fabiana',
 'unlicensed',
 'lightfoot',
 'selftalkyou',
 'looks',
 'tensematching',
 'underquantified',
 'wendy',
 'inceleyerek',
 'proving',
 'marieluise',
 'lapolla',
 'branchacc',
 'remoteness',
 'semantik',
 'sculpting',

In [89]:
joblib.dump(authors_flat, 'authors')

['authors']